<h1>CycleGAN for Style Transfer</h1>
<h3> Imports </h3>

In [1]:
#Python imports
import torch
import torch.nn as tnn
from torch.autograd import Variable
import sys
import itertools
from torch.utils.data import DataLoader
from Dataset import ImageSet
import datetime
import torchvision.utils as tv
import os
import matplotlib.pyplot as plt
import numpy as np

#Import network elements
import network_elements as net

#stdout code blocks reload's print statement
#prevstd = sys.stdout
#sys.stdout = None
reload(net)
print("Reloading net")
#sys.stdout = prevstd

Reloading net


<h3>Set parameters</h3>

In [2]:
#The number of channels in the input image
im_in_channels = 3

#The number of channels in the output image
im_out_channels = 3

#The size of the largest size of the input image
im_size = 128

LEARNING_RATE = 0.0002

LR_DECAY_START = 100
LR_DECAY_END = 200
NUM_EPOCHS = 200

load_partial_net = True
CURR_EPOCH = 0

<h3>Import dataset</h3>

In [3]:
# apple2orange, summer2winter_yosemite, horse2zebra, monet2photo, cezanne2photo, ukiyoe2photo, vangogh2photo, maps, cityscapes, facades, iphone2dslr_flower, ae_photos"
imageSet = ImageSet();
dataset = "ukiyoe2photo"
imageSet.loadData(dataset, 'train', im_size)
imgLoader = DataLoader(imageSet,shuffle=True)

./datasets/ukiyoe2photo
Finished loading data


<h3>Define the CycleGAN network</h3>

In [4]:
#G : X->Y
G = net.Mapping(im_in_channels, im_out_channels, im_size)

#F : Y->X
F = net.Mapping(im_out_channels, im_out_channels, im_size)

#G mapping discriminator
Dx = net.Discriminator(im_in_channels)

#F mapping discriminator
Dy = net.Discriminator(im_out_channels)

#Initialize CUDA implementations
G.cuda();
F.cuda();
Dx.cuda();
Dy.cuda();

#Define losses
cycle_loss = tnn.L1Loss(); #Cycle-consistency loss
gan_loss = tnn.MSELoss(); #Adversarial loss
identity_loss = tnn.L1Loss(); #Prevents image tinting

<h3>Initialize weights for each network</h3>

In [5]:
# norm_weights function applies Gaussian norm weights with mean 0 and stddev 0.02
G.apply(net.conv_norm_weights);
F.apply(net.conv_norm_weights);
Dx.apply(net.conv_norm_weights);
Dy.apply(net.conv_norm_weights);

<h3>Set optimizer parameters</h3>

In [6]:
#simplified version has no pooling, paper does not, paper code does...
# REMOVE

gan_opt = torch.optim.Adam(itertools.chain(G.parameters(), F.parameters()),
                           lr = LEARNING_RATE)
dx_opt = torch.optim.Adam(Dx.parameters(), lr = LEARNING_RATE)
dy_opt = torch.optim.Adam(Dy.parameters(), lr = LEARNING_RATE)

The paper uses Adam optimizer with a learning rate of 0.0002 for the first 100 epochs that linearly decays to 0 over the next 100 epochs.

<h3> Initialize training variables </h3>

In [7]:
x = torch.cuda.FloatTensor(1, im_in_channels, im_size, im_size)
y = torch.cuda.FloatTensor(1, im_out_channels, im_size, im_size)

# Variable wrapper is depricated in >0.4
dReal = Variable(torch.cuda.FloatTensor(1).fill_(1.0), requires_grad = False)
dFake = Variable(torch.cuda.FloatTensor(1).fill_(0.0), requires_grad = False)

buffX_Y = net.MapBuffer()
buffY_X = net.MapBuffer()

if not os.path.isdir("./img/"):
    os.mkdir("./img/")

if not os.path.isdir("./img/" + dataset + "/"):
    os.mkdir("./img/" + dataset + '/')
    
if not os.path.isdir("./log/"):
    os.mkdir("./log")
    
if not os.path.isdir("./log/" + dataset + "/"):
    os.mkdir("./log/" + dataset + "/")
    
if os.path.isfile("./log/" + dataset + "/loss.log") and not load_partial_net:    
    os.remove("./log/" + dataset + "/loss.log")
    
logfile = open("./log/" + dataset + "/loss.log","a")

<h3> Load Partial Net </h3>

In [8]:
if (load_partial_net):
    if os.path.isfile("./model/" + dataset + "/model_info.txt"):
        model_file = open("./model/" + dataset + "/model_info.txt", "r")
        CURR_EPOCH = int(model_file.read())
        model_file.close()
    G.load_state_dict(torch.load('./model/' + dataset + '/G.data'))
    F.load_state_dict(torch.load('./model/' + dataset + '/F.data'))
    Dx.load_state_dict(torch.load('./model/' + dataset + '/Dx.data'))
    Dy.load_state_dict(torch.load('./model/' + dataset + '/Dy.data'))
    gan_opt.load_state_dict(torch.load('./model/' + dataset + '/gan_opt.data'))
    dx_opt.load_state_dict(torch.load('./model/' + dataset + '/dx_opt.data'))
    dy_opt.load_state_dict(torch.load('./model/' + dataset + '/dy_opt.data'))
    
last_epoch = -1
if (load_partial_net):
    last_epoch = CURR_EPOCH-1

gan_lr = torch.optim.lr_scheduler.LambdaLR(gan_opt, net.LRDecay(LR_DECAY_START, LR_DECAY_END).step, last_epoch)
dx_lr = torch.optim.lr_scheduler.LambdaLR(dx_opt, net.LRDecay(LR_DECAY_START, LR_DECAY_END).step, last_epoch)
dy_lr = torch.optim.lr_scheduler.LambdaLR(dy_opt, net.LRDecay(LR_DECAY_START, LR_DECAY_END).step, last_epoch)

<h3> Training </h3>

In [ ]:
start_time = datetime.datetime.now()
for i in range(CURR_EPOCH,NUM_EPOCHS):
    for j, img in enumerate(imgLoader):
        elapsed_time = datetime.datetime.now()-start_time
        print("Epoch %d/%d, %d/%d, %s"%(i,LR_DECAY_END,j,len(imageSet),str(elapsed_time)))
        src_x = Variable(x.copy_(img['x']))
        src_y = Variable(y.copy_(img['y']))
        
        gan_opt.zero_grad()
        
        #identity Loss
        mapY_Y = G(src_y)
        lossY_Y = identity_loss(mapY_Y, src_y)*5.0
        
        mapX_X = F(src_x)
        lossX_X = identity_loss(mapX_X, src_x)*5.0
        
        #GAN Loss
        mapX_Y = G(src_x) #Generate image Y' from image X
        dX_Y = Dy(mapX_Y) #Check if image Y' seems real
        lossX_Y = gan_loss(dX_Y, dReal) #Calculate Y' realism error
        
        mapY_X = F(src_y) #Generate image X' from image Y
        dY_X = Dx(mapY_X) #Check if image X' seems real
        lossY_X = gan_loss(dY_X, dReal) #Calculate X' realism error
        
        #Cycle Consistency Loss
        mapX_Y_X = F(mapX_Y)
        lossX_Y_X = cycle_loss(mapX_Y_X, src_x)*10.0
        
        mapY_X_Y = G(mapY_X)
        lossY_X_Y = cycle_loss(mapY_X_Y, src_y)*10.0
        
        mapLoss = lossY_Y + lossX_X + lossX_Y + lossY_X + lossX_Y_X + lossY_X_Y
        mapLoss.backward()
        
        gan_opt.step()
        
        #Dx
        dx_opt.zero_grad()
        
        dX_res = Dx(src_x)
        lossX = gan_loss(dX_res, dReal)
        
        mapY_X_old = buffY_X.cycle(mapY_X)
        dY_X = Dx(mapY_X_old.detach())
        lossY_X = gan_loss(dY_X, dFake)
        
        dxLoss = (lossX + lossY_X)*0.5
        dxLoss.backward()
        
        dx_opt.step()
        
        #Dy
        dy_opt.zero_grad()
        
        dY_res = Dy(src_y)
        lossY = gan_loss(dY_res, dReal)
        
        mapX_Y_old = buffX_Y.cycle(mapX_Y)
        dX_Y = Dy(mapX_Y_old.detach())
        lossX_Y = gan_loss(dX_Y, dFake)
        
        dyLoss = (lossY + lossX_Y)*0.5
        dyLoss.backward()
        
        dy_opt.step()     
        
        print("%d,%d,%f,%f,%f,%f,%f\n"%(i,j,mapLoss.data[0], 
                                          (lossX_X+lossY_Y).data[0], 
                                          (lossX_Y+lossY_X).data[0], 
                                          (lossX_Y_X+lossY_X_Y).data[0], 
                                          (dxLoss+dyLoss).data[0]))
        
        logfile.write("%d,%d,%f,%f,%f,%f,%f\n"%(i,j,mapLoss.data[0], 
                                          (lossX_X+lossY_Y).data[0], 
                                          (lossX_Y+lossY_X).data[0], 
                                          (lossX_Y_X+lossY_X_Y).data[0], 
                                          (dxLoss+dyLoss).data[0]))
        
    tv.save_image(src_x.data, './img/' + dataset + '/src_x_%d.jpg'%(i))
    tv.save_image(src_y.data, './img/' + dataset + '/src_y_%d.jpg'%(i))
    tv.save_image(mapX_Y.data, './img/' + dataset + '/mapX_Y_%d.jpg'%(i))
    tv.save_image(mapY_X.data, './img/' + dataset + '/mapY_X_%d.jpg'%(i))
    gan_lr.step()
    dx_lr.step()
    dy_lr.step()
    

    if not os.path.isdir("./model/"):
        os.mkdir("./model/")
    
    if not os.path.isdir("./model/" + dataset + "/"):
        os.mkdir("./model/" + dataset + "/")
    model_file = open("./model/" + dataset + "/model_info.txt", "w")
    model_file.write("%d"%(i+1))
    model_file.close()
    torch.save(G.state_dict(), './model/' + dataset + '/G.data')
    torch.save(F.state_dict(), './model/' + dataset + '/F.data')
    torch.save(Dx.state_dict(), './model/' + dataset + '/Dx.data')
    torch.save(Dy.state_dict(), './model/' + dataset + '/Dy.data')
    torch.save(gan_opt.state_dict(), './model/' + dataset + '/gan_opt.data')
    torch.save(dx_opt.state_dict(), './model/' + dataset + '/dx_opt.data')
    torch.save(dy_opt.state_dict(), './model/' + dataset + '/dy_opt.data')

Epoch 56/200, 0/6287, 0:00:00.083774
56,0,4.708795,0.853881,0.047412,2.203510,0.067455

Epoch 56/200, 1/6287, 0:00:02.169094
56,1,3.367633,0.745901,0.305837,1.877980,0.159687

Epoch 56/200, 2/6287, 0:00:02.381297
56,2,3.469207,0.721195,0.363104,1.949709,0.185630

Epoch 56/200, 3/6287, 0:00:02.552364
56,3,3.811457,0.706563,0.188807,2.055045,0.104664

Epoch 56/200, 4/6287, 0:00:02.714825
56,4,3.916570,0.772389,0.128320,1.997183,0.139042

Epoch 56/200, 5/6287, 0:00:02.876711
56,5,5.336551,0.758155,0.091885,3.252575,0.080303

Epoch 56/200, 6/6287, 0:00:03.038209
56,6,4.184802,0.660745,0.018556,1.890155,0.149913

Epoch 56/200, 7/6287, 0:00:03.199515
56,7,6.612543,1.076401,0.126583,2.421120,0.150322

Epoch 56/200, 8/6287, 0:00:03.360860
56,8,5.206094,0.777277,0.076216,2.412548,0.226939

Epoch 56/200, 9/6287, 0:00:03.517429
56,9,8.292297,1.716137,0.058819,3.831889,0.064812

Epoch 56/200, 10/6287, 0:00:03.678235
56,10,5.481281,1.234159,0.050371,2.110610,0.079693

Epoch 56/200, 11/6287, 0:00:03

56,92,3.899441,0.690375,0.073864,2.010916,0.045168

Epoch 56/200, 93/6287, 0:00:16.782062
56,93,3.782031,0.727471,0.155979,1.969805,0.101755

Epoch 56/200, 94/6287, 0:00:16.947994
56,94,3.948920,0.778669,0.154859,2.105775,0.127272

Epoch 56/200, 95/6287, 0:00:17.122672
56,95,3.643360,0.744282,0.104829,1.930886,0.199930

Epoch 56/200, 96/6287, 0:00:17.287901
56,96,3.756294,0.625523,0.033976,1.847988,0.102846

Epoch 56/200, 97/6287, 0:00:17.456098
56,97,4.707567,1.098074,0.099672,2.620884,0.106623

Epoch 56/200, 98/6287, 0:00:17.607350
56,98,4.782313,1.260741,0.044272,2.281361,0.031923

Epoch 56/200, 99/6287, 0:00:17.761980
56,99,4.518940,0.772731,0.023015,2.060276,0.055906

Epoch 56/200, 100/6287, 0:00:17.936297
56,100,4.556217,1.117841,0.525225,2.567328,0.376634

Epoch 56/200, 101/6287, 0:00:18.100308
56,101,3.983939,0.716601,0.108750,1.988558,0.303898

Epoch 56/200, 102/6287, 0:00:18.277737
56,102,4.211586,0.790427,0.169587,2.454647,0.252076

Epoch 56/200, 103/6287, 0:00:18.441497
56,

56,182,3.799078,0.615289,0.162500,1.604265,0.136251

Epoch 56/200, 183/6287, 0:00:31.464950
56,183,3.960216,0.693544,0.061080,2.039686,0.156072

Epoch 56/200, 184/6287, 0:00:31.630029
56,184,3.934564,0.787952,0.040195,1.861606,0.086643

Epoch 56/200, 185/6287, 0:00:31.800417
56,185,4.798575,0.959634,0.174751,2.608714,0.214670

Epoch 56/200, 186/6287, 0:00:31.965312
56,186,3.539060,0.528104,0.130050,1.440906,0.237966

Epoch 56/200, 187/6287, 0:00:32.137811
56,187,4.824513,0.904319,0.135357,2.190871,0.104370

Epoch 56/200, 188/6287, 0:00:32.314822
56,188,4.056854,0.774694,0.059576,2.123968,0.064328

Epoch 56/200, 189/6287, 0:00:32.483749
56,189,4.661825,1.178283,0.261173,2.555838,0.145506

Epoch 56/200, 190/6287, 0:00:32.653386
56,190,3.857717,0.653885,0.033824,2.023475,0.053164

Epoch 56/200, 191/6287, 0:00:32.819318
56,191,4.791810,0.813304,0.003119,2.237315,0.258760

Epoch 56/200, 192/6287, 0:00:32.985337
56,192,8.118009,2.439174,0.032868,4.151283,0.083267

Epoch 56/200, 193/6287, 0:0

56,272,4.092958,0.966618,0.272956,1.936991,0.334092

Epoch 56/200, 273/6287, 0:00:46.354471
56,273,4.856561,1.075982,0.172397,2.652004,0.107643

Epoch 56/200, 274/6287, 0:00:46.497123
56,274,3.604897,0.718105,0.132645,1.962700,0.191236

Epoch 56/200, 275/6287, 0:00:46.644153
56,275,4.026079,0.747641,0.062817,1.945032,0.053062

Epoch 56/200, 276/6287, 0:00:46.815061
56,276,6.029783,1.169268,0.006368,2.710247,0.005401

Epoch 56/200, 277/6287, 0:00:46.983437
56,277,3.740807,0.678053,0.052242,1.748233,0.155815

Epoch 56/200, 278/6287, 0:00:47.155480
56,278,5.107308,1.160072,0.061824,2.547447,0.048505

Epoch 56/200, 279/6287, 0:00:47.317252
56,279,3.711013,0.881575,0.162632,1.798972,0.107108

Epoch 56/200, 280/6287, 0:00:47.486775
56,280,4.347392,0.693631,0.066708,2.214658,0.050795

Epoch 56/200, 281/6287, 0:00:47.646154
56,281,4.328591,0.917341,0.119081,2.266015,0.079047

Epoch 56/200, 282/6287, 0:00:47.811488
56,282,6.206378,0.837517,0.076062,3.391634,0.203860

Epoch 56/200, 283/6287, 0:0

56,363,3.754922,0.751234,0.172546,2.001497,0.141831

Epoch 56/200, 364/6287, 0:01:01.387421
56,364,3.622218,0.755022,0.356552,2.006083,0.232720

Epoch 56/200, 365/6287, 0:01:01.542515
56,365,4.062674,0.729746,0.220533,2.095462,0.121104

Epoch 56/200, 366/6287, 0:01:01.693243
56,366,4.910521,0.976035,0.080872,2.507608,0.189803

Epoch 56/200, 367/6287, 0:01:01.834888
56,367,4.231555,0.946043,0.001645,2.025186,0.172037

Epoch 56/200, 368/6287, 0:01:01.987960
56,368,4.997459,0.841424,0.024831,2.301334,0.078040

Epoch 56/200, 369/6287, 0:01:02.144080
56,369,5.565893,0.978777,0.041501,2.310387,0.230267

Epoch 56/200, 370/6287, 0:01:02.305383
56,370,3.938033,0.651268,0.211587,1.755878,0.175214

Epoch 56/200, 371/6287, 0:01:02.478591
56,371,3.731419,0.815354,0.396458,2.036898,0.238582

Epoch 56/200, 372/6287, 0:01:02.655809
56,372,3.678399,0.767516,0.105133,1.819978,0.082379

Epoch 56/200, 373/6287, 0:01:02.823624
56,373,3.633946,0.617239,0.108668,1.896724,0.083757

Epoch 56/200, 374/6287, 0:0

...

67,1355,5.055420,0.661241,0.100654,1.946080,0.217165

Epoch 67/200, 1356/6287, 3:15:58.893312
67,1356,3.591619,0.593208,0.055177,1.708171,0.570903

Epoch 67/200, 1357/6287, 3:15:59.062583
67,1357,5.181049,0.879394,0.035633,2.243515,0.093463

Epoch 67/200, 1358/6287, 3:15:59.221239
67,1358,4.087115,0.826152,0.132672,1.721691,0.075212

Epoch 67/200, 1359/6287, 3:15:59.395927
67,1359,5.277903,1.002402,0.105438,2.278420,0.146422

Epoch 67/200, 1360/6287, 3:15:59.562476
67,1360,4.725228,0.840987,0.167678,2.181896,0.085674

Epoch 67/200, 1361/6287, 3:15:59.731769
67,1361,4.197660,0.861381,0.200941,1.900488,0.140340

Epoch 67/200, 1362/6287, 3:15:59.910526
67,1362,3.518832,0.572262,0.179859,1.605292,0.193484

Epoch 67/200, 1363/6287, 3:16:00.081548
67,1363,4.318487,0.724441,0.146678,2.120151,0.125240

Epoch 67/200, 1364/6287, 3:16:00.242312
67,1364,3.474318,0.769393,0.075460,1.830025,0.038521

Epoch 67/200, 1365/6287, 3:16:00.401382
67,1365,3.281836,0.690942,0.089886,1.517957,0.141198

Epoch 

67,1443,3.696044,0.777260,0.434161,2.198107,0.222457

Epoch 67/200, 1444/6287, 3:16:13.623188
67,1444,4.283934,0.789098,0.227001,1.903527,0.137882

Epoch 67/200, 1445/6287, 3:16:13.789383
67,1445,5.498105,1.061934,0.158595,2.892422,0.324685

Epoch 67/200, 1446/6287, 3:16:13.958141
67,1446,4.022293,0.721940,0.007093,1.992319,0.169277

Epoch 67/200, 1447/6287, 3:16:14.122859
67,1447,5.070218,1.100310,0.132531,2.401861,0.129144

Epoch 67/200, 1448/6287, 3:16:14.298772
67,1448,4.753109,0.783523,0.175804,2.621543,0.174383

Epoch 67/200, 1449/6287, 3:16:14.474712
67,1449,4.026856,0.775003,0.034087,2.295141,0.052097

Epoch 67/200, 1450/6287, 3:16:14.651807
67,1450,3.076709,0.595819,0.243351,1.751333,0.143841

Epoch 67/200, 1451/6287, 3:16:14.822837
67,1451,3.233444,0.484458,0.056662,1.811101,0.054545

Epoch 67/200, 1452/6287, 3:16:14.990346
67,1452,2.421476,0.475563,0.069628,1.360349,0.096758

Epoch 67/200, 1453/6287, 3:16:15.162043
67,1453,3.074816,0.627189,0.063606,1.507964,0.125559

Epoch 

67,1531,3.631406,0.711854,0.196849,1.905381,0.238384

Epoch 67/200, 1532/6287, 3:16:28.480144
67,1532,3.254951,0.635152,0.019241,1.536717,0.013800

Epoch 67/200, 1533/6287, 3:16:28.654989
67,1533,4.822039,0.836213,0.014126,2.297866,0.328950

Epoch 67/200, 1534/6287, 3:16:28.828769
67,1534,3.067605,0.614622,0.118806,1.695936,0.189353

Epoch 67/200, 1535/6287, 3:16:28.993681
67,1535,3.287081,0.581072,0.629036,1.639238,0.327568

Epoch 67/200, 1536/6287, 3:16:29.176960
67,1536,4.587567,0.781647,0.018930,2.197419,0.045258

Epoch 67/200, 1537/6287, 3:16:29.344024
67,1537,4.644824,0.627716,0.209955,2.055445,0.144767

Epoch 67/200, 1538/6287, 3:16:29.510152
67,1538,4.617357,0.748078,0.070301,2.271401,0.062409

Epoch 67/200, 1539/6287, 3:16:29.676887
67,1539,2.976838,0.427891,0.161864,1.566185,0.118616

Epoch 67/200, 1540/6287, 3:16:29.838244
67,1540,3.198810,0.825569,0.061938,1.282018,0.215190

Epoch 67/200, 1541/6287, 3:16:30.009993
67,1541,3.819639,0.723292,0.243368,2.112952,0.252381

Epoch 

67,1619,3.463283,0.447710,0.025933,1.415250,0.116530

Epoch 67/200, 1620/6287, 3:16:43.276462
67,1620,3.118171,0.532068,0.012000,1.520266,0.007561

Epoch 67/200, 1621/6287, 3:16:43.454800
67,1621,5.282985,1.046329,0.007605,2.702508,0.070825

Epoch 67/200, 1622/6287, 3:16:43.629349
67,1622,3.618041,0.613873,0.341365,2.098145,0.198949

Epoch 67/200, 1623/6287, 3:16:43.796042
67,1623,4.183747,0.851438,0.127420,1.962639,0.069171

Epoch 67/200, 1624/6287, 3:16:43.973517
67,1624,3.952148,0.651245,0.001821,1.737787,0.033867

Epoch 67/200, 1625/6287, 3:16:44.146304
67,1625,5.016325,0.833253,0.036057,2.379094,0.156045

Epoch 67/200, 1626/6287, 3:16:44.313259
67,1626,3.797819,0.697188,0.050063,1.715966,0.040526

Epoch 67/200, 1627/6287, 3:16:44.489423
67,1627,4.249616,0.668453,0.030202,1.615726,0.060740

Epoch 67/200, 1628/6287, 3:16:44.665146
67,1628,4.380788,0.842435,0.009459,1.803393,0.059021

Epoch 67/200, 1629/6287, 3:16:44.831184
67,1629,2.923888,0.484532,0.001058,1.378303,0.040521

Epoch 

67,1707,4.893285,0.778253,0.170899,2.096078,0.125837

Epoch 67/200, 1708/6287, 3:16:58.066478
67,1708,4.017004,0.941653,0.143914,1.770471,0.102150

Epoch 67/200, 1709/6287, 3:16:58.224051
67,1709,4.301162,0.619559,0.009920,1.906010,0.052759

Epoch 67/200, 1710/6287, 3:16:58.398042
67,1710,3.895905,0.683297,0.206051,2.266970,0.155488

Epoch 67/200, 1711/6287, 3:16:58.575655
67,1711,4.101779,0.663967,0.019296,1.811409,0.037517

Epoch 67/200, 1712/6287, 3:16:58.745947
67,1712,3.054833,0.744601,0.059708,1.857549,0.066297

Epoch 67/200, 1713/6287, 3:16:58.918354
67,1713,4.462163,0.689533,0.015472,2.094350,0.188503

Epoch 67/200, 1714/6287, 3:16:59.074962
67,1714,3.889557,0.682188,0.059593,1.779145,0.037445

Epoch 67/200, 1715/6287, 3:16:59.239161
67,1715,3.366303,0.549349,0.088878,1.190241,0.079589

Epoch 67/200, 1716/6287, 3:16:59.414179
67,1716,3.299608,0.736718,0.017548,1.492899,0.075887

Epoch 67/200, 1717/6287, 3:16:59.584155
67,1717,4.564460,1.062951,0.177893,1.858959,0.159598

Epoch 

In [ ]:
close(logfile)